In [9]:
import torch
import numpy as np
#from data.patientHandler import patientReal
from sklearn.preprocessing import MinMaxScaler

allTimeSeries=torch.load("data/192T/data2.pt")
allMasks=torch.load("data/192T/masks2.pt")
allDiffs=torch.load("data/192T/diffs2.pt")
allLabels=torch.load("data/192T/labels2.pt")

In [10]:
def patientReal(patient, patientMasks, numTimeSteps):

    realPatient = []
    for k in range(numTimeSteps):
        if(patientMasks[k]==0):
            realPatient.append(patient[k])
    return realPatient          #output shape 192 x 1

In [16]:
#following code finds outliers for each patient and medical variable
#based on outlier value and medical variable, it will be decided if outlier should be deleted or not

def findOutliers(series, masks, diffs, numPatients, numTimeSteps, numVariables):
    #series, masks, diffs are tensors (6261, 192, 58)
    
    series, masks, diffs = np.asarray(series), np.asarray(masks), np.asarray(diffs)
     
    cleanSeries3DMatrix = []
    for n in range(numPatients):
        cleanSeriesPerPatient = []
        for i in range(numVariables):
            cleanSeriesPerVariable = []
            seriesPerVariable = series[n,:,i]
            if(np.sum(masks[n,:,i])==192):
                realPatient = seriesPerVariable
                cleanSeriesPerVariable = realPatient
            else:
                realPatient = patientReal(seriesPerVariable, masks[n,:,i], numTimeSteps) 
                mean = np.mean(realPatient)
                #std = np.std(realPatient)
                q98, q02 = np.percentile(observationsForVariable, [98 ,2])
                boundSet = (q02, q98)
                for j in range(numTimeSteps):
                    observation = seriesPerVariable[j]
                    
                    #CONDITIONS FOR IF STATEMENT WILL HVE TO CHANGE
                    if(observation >= boundSet[0] and observation <= boundSet[1]):
                        cleanSeriesPerVariable.append(observation)
                    else:
                        print('patient: ', n, ' variable: ', i, ' outlier index: ', j )
                        print('variable range (2 std): ', boundSet)
                        print('outlier value: ', observation)
                        cleanSeriesPerVariable.append(0)
                        masks[n][j][i] = 1
                        if(j==0):
                            diffs[n][j][i] = 0
                        else:
                            diffs[n][j][i] = (diffs[n][j-1][i] + 1/48)
            cleanSeriesPerPatient.append(cleanSeriesPerVariable)

        cleanSeries3DMatrix.append(np.asarray(cleanSeriesPerPatient))
        
    cleanSeries3DMatrix = torch.from_numpy(np.asarray(cleanSeries3DMatrix))
    cleanSeries3DMatrix = torch.transpose(cleanSeries3DMatrix, 1, 2)
    
    return cleanSeries3DMatrix, masks, diffs   #outputs tensors

In [18]:
#series, masks, diffs = findOutliers(allTimeSeries, allMasks, allDiffs, 10, 192, 59)

patient:  0  variable:  15  outlier index:  0
variable range (2 std):  (46.20000076293945, 46.20000076293945)
outlier value:  0.0
patient:  0  variable:  15  outlier index:  1
variable range (2 std):  (46.20000076293945, 46.20000076293945)
outlier value:  0.0
patient:  0  variable:  15  outlier index:  3
variable range (2 std):  (46.20000076293945, 46.20000076293945)
outlier value:  0.0
patient:  0  variable:  15  outlier index:  4
variable range (2 std):  (46.20000076293945, 46.20000076293945)
outlier value:  0.0
patient:  0  variable:  15  outlier index:  5
variable range (2 std):  (46.20000076293945, 46.20000076293945)
outlier value:  0.0
patient:  0  variable:  15  outlier index:  6
variable range (2 std):  (46.20000076293945, 46.20000076293945)
outlier value:  0.0
patient:  0  variable:  15  outlier index:  7
variable range (2 std):  (46.20000076293945, 46.20000076293945)
outlier value:  0.0
patient:  0  variable:  15  outlier index:  8
variable range (2 std):  (46.20000076293945,

In [33]:
#finds central 2std range for each variable across all patients
#does not give range for variables 0-13 because there are too few patients with observations

#for variables 0-13: check if any patients have outliers (observations outside 2 std range)

def variableAnalysis(series, masks, numPatients, numTimeSteps, numVariables): 
    #input shape (6261, 192, 59)
    allRealObservations = []   #final shape ( < 192x6261) x (58-14-1)
    
    for i in range(numVariables):
        observationsForVariable = []    #shape ( < 192x6261)
        negativeTicker = 0 
        zeroTicker = 0
        closeToZeroTicker = 0
        outlierTicker = 0
        negativeOutlierTicker = 0
        zeroOutlierTicker = 0
        lowerOutlierTicker = 0
        extLowerOutlierTicker = 0
        upperOutlierTicker = 0
        extUpperOutlierTicker = 0
        
        if (i<=13 or i==19):
            pass
        else:
            for n in range(numPatients):
                realSeriesPerPatient = patientReal(series[n,:,i], masks[n,:,i], numTimeSteps)
                for obs in realSeriesPerPatient:
                    observationsForVariable.append(obs)
            
            observationsForVariable = np.array(observationsForVariable)
            observationsForVarCount = len(observationsForVariable)
            mean = np.mean(observationsForVariable, dtype=np.float64)
            std = np.std(observationsForVariable, dtype=np.float64)
            q98, q02 = np.percentile(observationsForVariable, [98 ,2])
            boundSet = (q02, q98)
            print('variable: ', i)
            print('range: ', boundSet)
            
            #determining outliers
            for obs in observationsForVariable:
                    if(obs < 0):
                        negativeTicker += 1
                    elif(obs==0):
                        zeroTicker += 1
                        #print('obs < .5*lowerBound: ', obs < .5*boundSet[0])
                    elif(0 < obs and obs < .5*boundSet[0]):
                        closeToZeroTicker += 1
                        
                    if(obs <= boundSet[0] or obs >= boundSet[1]):
                        outlierTicker += 1
                        if (obs < 0):
                            negativeOutlierTicker +=1
                        elif (obs == 0):
                            zeroOutlierTicker +=1
                        elif(obs<=boundSet[0]):
                            lowerOutlierTicker += 1
                            if(obs<=(mean-3.3*std)):
                                extLowerOutlierTicker +=1
                                #print('ext lower bound: ', mean-3.3*std)
                        elif(obs>=boundSet[1]):
                            upperOutlierTicker += 1
                            if(obs>=(mean+3.3*std)):
                                extUpperOutlierTicker +=1
             
            #what percent of real observations are negative?
            print('proportion:  negative obs / real observations: ', negativeTicker/observationsForVarCount)
            print('proportion:  zero obs / real observations: ', zeroTicker/observationsForVarCount)
            print('proportion:  close-to zero obs / real observations: ', closeToZeroTicker/observationsForVarCount)
            print()
            
            #what proportion of real observations are outliers?
            print('proportion:  outliers / real observations: ', outlierTicker/observationsForVarCount)
            if (outlierTicker == 0):
                pass
            else:
                #what proportion of outliers are negative, zero, other?
                print('proportion:  neg outliers / outliers: ', negativeOutlierTicker/outlierTicker)
                print('proportion:  zero outliers / outliers: ', zeroOutlierTicker/outlierTicker)
                print('proportion:  lower outliers / outliers: ', lowerOutlierTicker/outlierTicker)
                print('proportion:  extreme lower outliers / outliers: ', extLowerOutlierTicker/outlierTicker)
                print('proportion:  upper outliers / outliers: ', upperOutlierTicker/outlierTicker)
                print('proportion:  extreme upper outliers / outliers: ', extUpperOutlierTicker/outlierTicker)
            print()
            print()

In [34]:
variableAnalysis(allTimeSeries, allMasks, 6261, 192, 59)

variable:  14
range:  (1.2999999523162842, 2.9000000953674316)
proportion:  negative obs / real observations:  0.0
proportion:  zero obs / real observations:  0.0
proportion:  close-to zero obs / real observations:  6.34981109311998e-05

proportion:  outliers / real observations:  0.04375019843159666
proportion:  neg outliers / outliers:  0.0
proportion:  zero outliers / outliers:  0.0
proportion:  lower outliers / outliers:  0.4593613933236575
proportion:  extreme lower outliers / outliers:  0.005805515239477504
proportion:  upper outliers / outliers:  0.5406386066763426
proportion:  extreme upper outliers / outliers:  0.14513788098693758


variable:  15
range:  (21.5, 45.599998474121094)
proportion:  negative obs / real observations:  0.0
proportion:  zero obs / real observations:  0.0
proportion:  close-to zero obs / real observations:  0.0001409741312469162

proportion:  outliers / real observations:  0.040365592913700336
proportion:  neg outliers / outliers:  0.0
proportion:  zero

In [5]:
def normalize(series, masks, diffs, numPatients, numTimeSteps, numVars):
    #series, masks, diffs are tensors (6261, 192, 58)
    
    scaler = MinMaxScaler()
    scaler.fit_transform(series)
    return series, masks, diffs          #outputs tensors

NameError: name 'normalize' is not defined

In [ ]:
series, mask, diffs = normalize(series, masks, diffs, 10, 192, 59)